# Investigating the Relationship Between Healthcare Coverage and  Expenditure on Heart Disease Mortality Across All States

   ### Geo Analysis
   
   Heart mortality is one of the leading causes of death in US & its prevention is a public health priority.
   Choropleth maps in plotly and folium is used to identify how well States with Higher Health spending per capita, the        uninsured population correlates to mortality due to various heart diseases. A sequential color scheme is used to 
   visually capture the outcomes and determinants in a choropleth map.     
   The objectives of this investigation were to: 
   1) Identify the states with highest deaths per capita and display them on a Stamen Toner choropleth map. 
   2) Display the distribution of Health spending across all 50 states(Average)  
   3) Display    the distribution of % Uninsured across all 50 states
   4) Visually identify whether States with the maximum uninsured population tend to have higher Deaths per capita(mortality rate) 
   5)Visually identify whether States with Highest spending per capita tend to have lower Deaths per capita (mortality rate). 

   Puerto Rico and District of Columbia were excluded from this analysis. 


In [7]:
# dependencies
import pandas as pd
import numpy as np
from pathlib import Path
import hvplot.pandas
import geopandas as gpd
import folium
import chart_studio.plotly as py
import plotly.offline as po
import plotly.graph_objs as pg
import matplotlib.pyplot as plt
%matplotlib inline

In [8]:
#dataset with US coordinates
us_state_coordinates_csv = "./Resources/us_state_coordinates.csv"

us_states_coordinates_df = pd.read_csv(us_state_coordinates_csv)
us_states_coordinates_df = us_states_coordinates_df.rename(columns={"name":"Location"})
us_states_coordinates_df.head()

Location  description   latitude   longitude
0     Alabama   Montgomery  32.377716  -86.300568
1      Alaska       Juneau  58.301598 -134.420212
2     Arizona      Phoenix  33.448143 -112.096962
3    Arkansas  Little Rock  34.746613  -92.288986
4  California   Sacramento  38.576668 -121.493629

In [9]:
# Spending File Pathing
health_spending_csv = Path("Resources/Health Care Expenditures per Capita by State of Residence raw data.csv")

#pd.read
spending_data = pd.read_csv(health_spending_csv,skiprows=[0,1])
spending_data = spending_data.dropna(axis=0,how='any',subset=["Health Spending per Capita"])
spending_data["Health Spending per Capita"] = spending_data["Health Spending per Capita"].str.replace(',', '').str.replace('$', '').astype(float)
spending_data.head()

C:\Users\bijoy\AppData\Local\Temp\ipykernel_10704\2385751765.py:7: FutureWarning:

The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.



Location  Health Spending per Capita
0  United States                      9671.0
1        Alabama                      8741.0
2         Alaska                     13226.0
3        Arizona                      8145.0
4       Arkansas                      8853.0

In [10]:
# Coverage File Pathing
health_coverage_csv = Path("Resources/Health Insurance Coverage of the Total Population raw data #.csv")

#pd.read
coverage_data = pd.read_csv(health_coverage_csv,skiprows=[0,1])
coverage_data = coverage_data.dropna(axis=0,how='any',subset=["Employer"])
#coverage_data["Employer"] = coverage_data["Employer"].map("{:,}".format)
#coverage_data["Non-Group"] = coverage_data["Non-Group"].map("{:,}".format)
#coverage_data["Medicaid"] = coverage_data["Medicaid"].map("{:,}".format)
#coverage_data["Medicare"] = coverage_data["Medicare"].map("{:,}".format)
#coverage_data["Military"] = coverage_data["Military"].map("{:,}".format)
#coverage_data["Uninsured"] = coverage_data["Uninsured"].map("{:,}".format)
#coverage_data["Total"] = coverage_data["Total"].map("{:,}".format)
coverage_data.head()

Location     Employer   Non-Group    Medicaid    Medicare   Military  \
0  United States  158000000.0  18728800.0  63145700.0  45286700.0  4393600.0   
1        Alabama    2250900.0    263400.0    929500.0    763800.0    99000.0   
2         Alaska     339800.0     24700.0    149400.0     70200.0    37100.0   
3        Arizona    3202000.0    366500.0   1489600.0   1145300.0   105600.0   
4       Arkansas    1226300.0    157300.0    767000.0    464200.0    41800.0   

    Uninsured        Total  Footnotes  
0  29349300.0  319000000.0        1.0  
1    460400.0    4767100.0        NaN  
2     80500.0     701700.0        NaN  
3    789100.0    7098000.0        NaN  
4    265800.0    2922500.0        NaN

In [11]:
# Merging
merged_per_state = pd.merge( spending_data, coverage_data, how="left", on=["Location", "Location"] )
merged_per_state.head()

Location  Health Spending per Capita     Employer   Non-Group  \
0  United States                      9671.0  158000000.0  18728800.0   
1        Alabama                      8741.0    2250900.0    263400.0   
2         Alaska                     13226.0     339800.0     24700.0   
3        Arizona                      8145.0    3202000.0    366500.0   
4       Arkansas                      8853.0    1226300.0    157300.0   

     Medicaid    Medicare   Military   Uninsured        Total  Footnotes  
0  63145700.0  45286700.0  4393600.0  29349300.0  319000000.0        1.0  
1    929500.0    763800.0    99000.0    460400.0    4767100.0        NaN  
2    149400.0     70200.0    37100.0     80500.0     701700.0        NaN  
3   1489600.0   1145300.0   105600.0    789100.0    7098000.0        NaN  
4    767000.0    464200.0    41800.0    265800.0    2922500.0        NaN

In [12]:
#Mortality File Pathing
hd_mortality_csv = Path("Resources/Heart Disease Mortality by State data table.csv")

#pd.read
mortaility_data = pd.read_csv(hd_mortality_csv)
mortaility_data = mortaility_data.loc[(mortaility_data["YEAR"] == 2019)]
mortaility_data = mortaility_data.reset_index(drop=True)
XX_to_full = {"AL":"Alabama",
              "AK":"Alaska",
              "AZ":"Arizona",
              "AR":"Arkansas",
              "CA":"California",
              "CO":"Colorado",
              "CT":"Connecticut",
              "DE":"Delaware",
              "DC":"District of Columbia",
              "FL":"Florida",
              "GA":"Georgia",
              "HI":"Hawaii",
              "ID":"Idaho",
              "IL":"Illinois",
              "IN":"Indiana",
              "IA":"Iowa",
              "KS":"Kansas",
              "KY":"Kentucky",
              "LA":"Louisiana",
              "ME":"Maine",
              "MD":"Maryland",
              "MA":"Massachusetts",
              "MI":"Michigan",
              "MN":"Minnesota",
              "MS":"Mississippi",
              "MO":"Missouri",
              "MT":"Montana",
              "NE":"Nebraska",
              "NV":"Nevada",
              "NH":"New Hampshire",
              "NJ":"New Jersey",
              "NM":"New Mexico",
              "NY":"New York",
              "NC":"North Carolina",
              "ND":"North Dakota",
              "MP":"Northern Mariana Islands",
              "OH":"Ohio",
              "OK":"Oklahoma",
              "OR":"Oregon",
              "PA":"Pennsylvania",
              "PR":"Puerto Rico",
              "RI":"Rhode Island",
              "SC":"South Carolina",
              "SD":"South Dakota",
              "TN":"Tennessee",
              "TX":"Texas",
              "UT":"Utah",
              "VT":"Vermont",
              "VA":"Virginia",
              "VI":"Virgin Islands",
              "WA":"Washington",
              "WV":"West Virginia",
              "WI":"Wisconsin",
              "WY":"Wyoming"}
mortaility_data["STATE"]=mortaility_data["STATE"].replace(XX_to_full)
mortaility_data = mortaility_data.rename(columns={"STATE":"Location"})
mortaility_data = mortaility_data.rename(columns={"YEAR":"Year"})
mortaility_data = mortaility_data.rename(columns={"RATE":"Deaths per 100k"})
mortaility_data = mortaility_data.rename(columns={"DEATHS":"Mortaility"})
mortaility_data["Mortaility"] = mortaility_data["Mortaility"].astype(float)
mortaility_data.head()

Year    Location  Deaths per 100k  Mortaility
0  2019     Alabama            219.6     13448.0
1  2019      Alaska            129.7       843.0
2  2019     Arizona            134.0     12587.0
3  2019    Arkansas            226.5      8669.0
4  2019  California            136.9     62394.0

In [13]:
#final merge
full_combined =  pd.merge( merged_per_state, mortaility_data, how="left", on=["Location", "Location"])
full_combined = full_combined.dropna(axis=0,how='any',subset=["Year"])
full_combined.head()

Location  Health Spending per Capita    Employer  Non-Group   Medicaid  \
1     Alabama                      8741.0   2250900.0   263400.0   929500.0   
2      Alaska                     13226.0    339800.0    24700.0   149400.0   
3     Arizona                      8145.0   3202000.0   366500.0  1489600.0   
4    Arkansas                      8853.0   1226300.0   157300.0   767000.0   
5  California                      9628.0  18538700.0  2569600.0  9790000.0   

    Medicare  Military  Uninsured       Total  Footnotes    Year  \
1   763800.0   99000.0   460400.0   4767100.0        NaN  2019.0   
2    70200.0   37100.0    80500.0    701700.0        NaN  2019.0   
3  1145300.0  105600.0   789100.0   7098000.0        NaN  2019.0   
4   464200.0   41800.0   265800.0   2922500.0        NaN  2019.0   
5  4388900.0  350200.0  3005400.0  38642700.0        NaN  2019.0   

   Deaths per 100k  Mortaility  
1            219.6     13448.0  
2            129.7       843.0  
3            134.0     12587.0  
4            226.5      8669.0  
5            136.9     62394.0

## Merging the US state coordinates dataset with the combined clean dataset. State coordinates are required for plotting geographical maps. 

In [14]:
full_combined_state_coords_df = pd.merge(full_combined,us_states_coordinates_df, how="left",left_on="Location",right_on="Location")
full_combined_state_coords_df.head()

Location  Health Spending per Capita    Employer  Non-Group   Medicaid  \
0     Alabama                      8741.0   2250900.0   263400.0   929500.0   
1      Alaska                     13226.0    339800.0    24700.0   149400.0   
2     Arizona                      8145.0   3202000.0   366500.0  1489600.0   
3    Arkansas                      8853.0   1226300.0   157300.0   767000.0   
4  California                      9628.0  18538700.0  2569600.0  9790000.0   

    Medicare  Military  Uninsured       Total  Footnotes    Year  \
0   763800.0   99000.0   460400.0   4767100.0        NaN  2019.0   
1    70200.0   37100.0    80500.0    701700.0        NaN  2019.0   
2  1145300.0  105600.0   789100.0   7098000.0        NaN  2019.0   
3   464200.0   41800.0   265800.0   2922500.0        NaN  2019.0   
4  4388900.0  350200.0  3005400.0  38642700.0        NaN  2019.0   

   Deaths per 100k  Mortaility  description   latitude   longitude  
0            219.6     13448.0   Montgomery  32.377716  -86.300568  
1            129.7       843.0       Juneau  58.301598 -134.420212  
2            134.0     12587.0      Phoenix  33.448143 -112.096962  
3            226.5      8669.0  Little Rock  34.746613  -92.288986  
4            136.9     62394.0   Sacramento  38.576668 -121.493629

##  Plot 1: Display states with highest number of Deaths per 100k(Top 5) 

States having highest Deaths per 100k were identified to be:

Oklahama, Mississippi, Arkansas, Alabama, Louisiana 

The indicators on the map used are icons in red with a plus sign 


In [15]:
#Top 5 states with highest number of Deaths per 100k

mortality_bystate_df = full_combined_state_coords_df.groupby(["Location","latitude","longitude"])["Deaths per 100k"].mean()
mortality_bystate_df = pd.DataFrame(mortality_bystate_df).reset_index().sort_values("Deaths per 100k",ascending=False )
#top 5
mortality_bystate_df.head()

Location   latitude  longitude  Deaths per 100k
35     Oklahoma  35.492207 -97.503342            231.4
23  Mississippi  32.303848 -90.182106            226.7
3      Arkansas  34.746613 -92.288986            226.5
0       Alabama  32.377716 -86.300568            219.6
17    Louisiana  30.457069 -91.187393            207.8

In [16]:
#plot the above data showing Top 5 states
#Used geospatial map plot options in folium library from python
#reference: https://www.analyticsvidhya.com/blog/2020/06/guide-geospatial-analysis-folium-python/

map = folium.Map(location=[mortality_bystate_df.latitude.mean(), mortality_bystate_df.longitude.mean()],
                 tiles= "Stamen Toner",zoom_start=5, control_scale=True)

#reference for adding titles: https://github.com/python-visualization/folium/issues/1202
title_html = '''
             <h3 align="center" style="font-size:20px"><b>Top 5 states by Deaths per 100k</b></h3>
             '''
map.get_root().html.add_child(folium.Element(title_html))

for index, location_info in mortality_bystate_df.head().iterrows():
    marker = folium.Marker([location_info["latitude"], location_info["longitude"]], 
                  popup="Deaths: " + str(location_info["Deaths per 100k"]), icon=folium.Icon(color="red"))
    marker.add_to(map)
    
map  

#map.save('Plot1-choropleth-map-with-folium.html')

## Analysis for Plot 2 and 3: 

It appears that States with lowest health spending per capita, tend to have higher uninsured % population. Hence Health spending per capita is somewhat related to Access to healthcare & support, however it also depends on size of the city and its population and also other economic factors may be involved which were not considered in this analysis. 

### Average Health spending per capita by State -  calculation



In [17]:
#Health spending per capita by State

#Creating a dictionary of state codes to merge it to the health spending dataframe
state_codes = {
    'District of Columbia' : 'dc','Mississippi': 'MS', 'Oklahoma': 'OK', 
    'Delaware': 'DE', 'Minnesota': 'MN', 'Illinois': 'IL', 'Arkansas': 'AR', 
    'New Mexico': 'NM', 'Indiana': 'IN', 'Maryland': 'MD', 'Louisiana': 'LA', 
    'Idaho': 'ID', 'Wyoming': 'WY', 'Tennessee': 'TN', 'Arizona': 'AZ', 
    'Iowa': 'IA', 'Michigan': 'MI', 'Kansas': 'KS', 'Utah': 'UT', 
    'Virginia': 'VA', 'Oregon': 'OR', 'Connecticut': 'CT', 'Montana': 'MT', 
    'California': 'CA', 'Massachusetts': 'MA', 'West Virginia': 'WV', 
    'South Carolina': 'SC', 'New Hampshire': 'NH', 'Wisconsin': 'WI',
    'Vermont': 'VT', 'Georgia': 'GA', 'North Dakota': 'ND', 
    'Pennsylvania': 'PA', 'Florida': 'FL', 'Alaska': 'AK', 'Kentucky': 'KY', 
    'Hawaii': 'HI', 'Nebraska': 'NE', 'Missouri': 'MO', 'Ohio': 'OH', 
    'Alabama': 'AL', 'Rhode Island': 'RI', 'South Dakota': 'SD', 
    'Colorado': 'CO', 'New Jersey': 'NJ', 'Washington': 'WA', 
    'North Carolina': 'NC', 'New York': 'NY', 'Texas': 'TX', 
    'Nevada': 'NV', 'Maine': 'ME'}

#merging 

health_spending_bystate_df = full_combined_state_coords_df.groupby(["Location","latitude","longitude"])["Health Spending per Capita"].mean()
health_spending_bystate_df = pd.DataFrame(health_spending_bystate_df).reset_index().sort_values("Health Spending per Capita",ascending=False )

#display the dataframe
health_spending_bystate_df.head()


Location   latitude   longitude  Health Spending per Capita
1          Alaska  58.301598 -134.420212                     13226.0
31       New York  42.652843  -73.757874                     12932.0
20  Massachusetts  42.358162  -71.063698                     12729.0
7        Delaware  39.157307  -75.519722                     12213.0
44        Vermont  44.262436  -72.580536                     12159.0

###  Plot 2: US - Average Health Spending per Capita - choropleth type

In [18]:

#reference for map plots using plotly and geopandas : 1) https://towardsdatascience.com/geographical-plotting-of-maps-with-plotly-4b5a5c95f02a
#                                                     2) https://plotly.com/python/choropleth-maps/

#initiate plotly’s notebook mode to display the plot inside the notebook.
#This will allow to generate graphs offline and save them in a local machine
po.init_notebook_mode(connected = True)

#adding a column for state code for the states in the health spending dataframe
health_spending_bystate_df['state_code'] = health_spending_bystate_df['Location'].apply(lambda x : state_codes[x])

#plotly iplot
data = dict(type = 'choropleth', 
            locations = health_spending_bystate_df['state_code'], 
            locationmode = 'USA-states', 
            z = health_spending_bystate_df['Health Spending per Capita'], 
            text = health_spending_bystate_df['Location'],
            colorbar = {'title' : 'Avg Health Spending'})


layout = dict(title = 'US States - Average Health Spending per Capita', 
              geo = dict(scope = 'usa'))
x = pg.Figure(data = [data], 
              layout = layout)

#display the figure
po.iplot(x)


## Plot 3: Percentage Unisured by State

In [19]:
#Calculate Uninsured Percentage by State and create a dataframe for uninsured percentage by Location

uninsured_pct_bystate_df = full_combined_state_coords_df[["Location","latitude","longitude","Uninsured","Total"]]
uninsured_pct_bystate_df["Uninsured Percentage"] = uninsured_pct_bystate_df["Uninsured"]/uninsured_pct_bystate_df["Total"]
uninsured_pct_bystate_df = pd.DataFrame(uninsured_pct_bystate_df).sort_values("Uninsured Percentage",ascending=False )
uninsured_pct_bystate_df = uninsured_pct_bystate_df.reset_index()
uninsured_pct_bystate_df = uninsured_pct_bystate_df.drop(columns="index")


#adding a column for state code for the states in the uninsured percentage dataframe
uninsured_pct_bystate_df['state_code'] = uninsured_pct_bystate_df['Location'].apply(lambda x : state_codes[x])

#plotly iplot
data = dict(type = 'choropleth', 
            locations = uninsured_pct_bystate_df['state_code'], 
            locationmode = 'USA-states', 
            z = 100 * uninsured_pct_bystate_df['Uninsured Percentage'], 
            text = uninsured_pct_bystate_df['Location'],
            colorscale = 'Reds',
            colorbar = {'title' : '% Uninsured'})


layout = dict(title = 'US States - Uninsured Percentage', 
              geo = dict(scope = 'usa'))
x = pg.Figure(data = [data], 
              layout = layout)
#display the figure
po.iplot(x)



C:\Users\bijoy\AppData\Local\Temp\ipykernel_10704\2475252549.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



##  Plot 4: Distribution of % Uninsured in comparison to States having least and highest deaths per 100k


As determined in Plot 1:
States with highest deaths per capita : Oklahoma, Mississippi, Arkansas, Alabama, Louisiana. In the map it is represented as Red plus icons. 
In this step we additionally determined the States with least Deaths per 100k by using the tail function in pandas dataframe: 

Alaska, Colorado, Massachusetts, Hawaii, Minnesota
In the map plot these are represented by the Blue plus icons. 

We extrapolated the above States with highest and least deaths per 100 k on a choropleth map in folium showing the distribution of % uninsured for all the US states. 

Hypothesis: 
States with the maximum uninsured population tend to have higher Deaths per capita (mortality rate).
It appears that the states with highest deaths per 100k due to heart diseases tends to have uninsured percent of 11-16 range but not the highest uninsured. 

As it appears from the map, Texas having maximum uninsured population, does not fall under the highest deaths per capita belt, because Texas being a bigger city, the infrastructure and medical facilities could be better and other economic factors which were not taken into account for this analysis.  The absolute mortality(deaths) in Texas will however be quite high, because of its population size. 

On the other hand, it appears that states that were identified with the least deaths per 100k fall in the bin of less uninsured population (access to better healthcare) – between 3% - 8%. 
However, other health indicators would be needed to investigate this further. 

In [20]:
#importing the Geojsontooltip module from folium features

from folium.features import GeoJsonTooltip


#reference for folium map plots: https://towardsdatascience.com/folium-and-choropleth-map-from-zero-to-pro-6127f9e68564
#reference for markers: https://towardsdatascience.com/folium-mapping-displaying-markers-on-a-map-6bd56f3e3420
                        #https://towardsdatascience.com/folium-mapping-displaying-markers-on-a-map-6bd56f3e3420
# choropleth map fill_color profiles: https://github.com/python-visualization/folium/issues/403

# Change Icons - https://getbootstrap.com/docs/3.3/components/#glyphicons-glyphs

#Read the geoJSON file using geopandas to fetch the geometry data and state_codes for merging later
geojson = gpd.read_file("./Resources/georef-united-states-of-america-state.geojson")
geojson.head()

PROJ: proj_create_from_database: Cannot find proj.db


geo_point_2d  year ste_code  \
0  {'lon': -120.5928034897229, 'lat': 47.41161380...  2022     [53]   
1  {'lon': -106.10844349925604, 'lat': 34.4212989...  2022     [35]   
2  {'lon': -71.50397526286355, 'lat': 42.16009070...  2022     [25]   
3  {'lon': -111.67824939585202, 'lat': 39.3237667...  2022     [49]   
4  {'lon': -92.43838227416394, 'lat': 34.89991914...  2022     [05]   

          ste_name ste_area_code ste_type ste_stusps_code  ste_fp_code  \
0     [Washington]           USA    state              WA          NaN   
1     [New Mexico]           USA    state              NM          NaN   
2  [Massachusetts]           USA    state              MA          NaN   
3           [Utah]           USA    state              UT          NaN   
4       [Arkansas]           USA    state              AR          NaN   

  ste_gnis_code                                           geometry  
0      01779804  POLYGON ((-117.03235 48.99920, -117.13490 48.9...  
1      00897535  POLYGON ((-106.52805 31.78389, -106.52706 31.7...  
2      00606926  POLYGON ((-71.08857 41.43131, -71.08504 41.433...  
3      01455989  POLYGON ((-114.04148 41.99387, -114.04137 41.9...  
4      00068085  POLYGON ((-91.16609 33.00429, -91.16637 33.010...

In [21]:
geojson=geojson[['ste_stusps_code','geometry']] #only select 'ste_stusps_code' and 'geometry' columns
geojson.sort_values("ste_stusps_code")
geojson.head()

ste_stusps_code                                           geometry
0              WA  POLYGON ((-117.03235 48.99920, -117.13490 48.9...
1              NM  POLYGON ((-106.52805 31.78389, -106.52706 31.7...
2              MA  POLYGON ((-71.08857 41.43131, -71.08504 41.433...
3              UT  POLYGON ((-114.04148 41.99387, -114.04137 41.9...
4              AR  POLYGON ((-91.16609 33.00429, -91.16637 33.010...

In [22]:
#merging the geojson dataframe with statecode and geometry with Unisured % by State dataframe
uninsured_map = geojson.merge(uninsured_pct_bystate_df,how="inner",left_on="ste_stusps_code",right_on="state_code")
uninsured_map = uninsured_map[~uninsured_map['geometry'].isna()]
uninsured_map = uninsured_map.dropna()
uninsured_map.head()


ste_stusps_code                                           geometry  \
0              WA  POLYGON ((-117.03235 48.99920, -117.13490 48.9...   
1              NM  POLYGON ((-106.52805 31.78389, -106.52706 31.7...   
2              MA  POLYGON ((-71.08857 41.43131, -71.08504 41.433...   
3              UT  POLYGON ((-114.04148 41.99387, -114.04137 41.9...   
4              AR  POLYGON ((-91.16609 33.00429, -91.16637 33.010...   

        Location   latitude   longitude  Uninsured      Total  \
0     Washington  47.035805 -122.905014   488900.0  7423900.0   
1     New Mexico  35.682240 -105.939728   200500.0  2041400.0   
2  Massachusetts  42.358162  -71.063698   202300.0  6650800.0   
3           Utah  40.777477 -111.888237   303700.0  3154100.0   
4       Arkansas  34.746613  -92.288986   265800.0  2922500.0   

   Uninsured Percentage state_code  
0              0.065855         WA  
1              0.098217         NM  
2              0.030417         MA  
3              0.096287         UT  
4              0.090950         AR

In [23]:

#make an empty map
us_map = folium.Map(location=[40, -96], zoom_start=4,tiles='Stamen Toner')



#Create the choropleth map add it to the base map
#States with highest Deaths per Capita vs % Uninsured population
#color scheme chosen yellow, orange and red

folium.Choropleth(
            geo_data="./Resources/georef-united-states-of-america-state.geojson",
            data=uninsured_map,
            columns=['state_code', 'Uninsured Percentage'],  #Here we tell folium to get the state codes and plot uninsured % for each state
            key_on='feature.properties.ste_stusps_code', #Here we grab the geometries/state boundaries from the geojson file using the key 'ste_stusps_code' which is the same as state code
            fill_color='YlOrRd',
            nan_fill_color="White", #Use white color if there is no data available for the state
            fill_opacity=0.7,
            line_opacity=0.2,
            legend_name='% Uninsured', 
            highlight=True,
            line_color='black').add_to(us_map) 

#reference for adding titles: https://github.com/python-visualization/folium/issues/1202
title_html = '''
             <h3 align="center" style="font-size:20px"><b>States representing highest and lowest Deaths per Capita vs % Uninsured by State</b></h3>
             '''
us_map.get_root().html.add_child(folium.Element(title_html))

#red-icons/ markers for states with highest deaths per capita = Top 5
for index, location_info in mortality_bystate_df.head().iterrows():
    marker = folium.Marker([location_info["latitude"], location_info["longitude"]], 
                  popup="Deaths per 100k: " + str(location_info["Deaths per 100k"]), icon=folium.Icon(color="red", icon="plus-sign"), 
                tooltip = "State: {}<br> Click for more".format(location_info["Location"]))
    marker.add_to(us_map)

#blue-icons/ markers for states with least deaths per capita = Bottom 5
for index, location_details in mortality_bystate_df.tail().iterrows():
    marker = folium.Marker([location_details["latitude"], location_details["longitude"]], 
                  popup="Deaths per 100k: " + str(location_details["Deaths per 100k"]), icon=folium.Icon(color="blue", 
                                                                                                         icon="plus-sign"), 
                tooltip = "State: {}<br> Click for more".format(location_details["Location"]))
    marker.add_to(us_map)    
    


us_map


#us_map.save('Plot 4-choropleth-map-with-folium.html')

##  Plot 5: Distribution of Average Health spending per capita and States with least and highest Deaths per 100k

We extrapolated the States with highest and least deaths per 100k on a choropleth map showing the distribution of average health spending for all the US states. 

Hypothesis: 
States with the highest spending per capita tend to have lower Deaths per capita (mortality rate).

It appears that the states with lowest deaths per 100k fall in the range of 9k to 13k(higher spending), AK being one of the states having the least Deaths per 100k and with Highest Average health spending. Hawaii being such a small island state, the Average Health spending is not very high however, the number of Deaths per 100K is less. However, for both Alaska and Hawaii, having less population due to its geographical location, could be one of the contributing factors to having least number of deaths per 100k. 

Other health indicators would be needed to investigate this further. 


In [24]:
#Reusing the dataframes previously created for avg health spending and avg Deaths per 100k by State,Latitude, Longitude 
health_spending_bystate_df.head()

Location   latitude   longitude  Health Spending per Capita  \
1          Alaska  58.301598 -134.420212                     13226.0   
31       New York  42.652843  -73.757874                     12932.0   
20  Massachusetts  42.358162  -71.063698                     12729.0   
7        Delaware  39.157307  -75.519722                     12213.0   
44        Vermont  44.262436  -72.580536                     12159.0   

   state_code  
1          AK  
31         NY  
20         MA  
7          DE  
44         VT

In [25]:
#Highest Deaths per 100k 
mortality_bystate_df.head()

Location   latitude  longitude  Deaths per 100k
35     Oklahoma  35.492207 -97.503342            231.4
23  Mississippi  32.303848 -90.182106            226.7
3      Arkansas  34.746613 -92.288986            226.5
0       Alabama  32.377716 -86.300568            219.6
17    Louisiana  30.457069 -91.187393            207.8

In [26]:
#Least Deaths per 100k 
mortality_bystate_df.tail()

Location   latitude   longitude  Deaths per 100k
1          Alaska  58.301598 -134.420212            129.7
5        Colorado  39.739227 -104.984856            127.7
20  Massachusetts  42.358162  -71.063698            127.2
10         Hawaii  21.307442 -157.857376            120.3
22      Minnesota  44.955097  -93.102211            116.7

In [27]:
geojson.head()

ste_stusps_code                                           geometry
0              WA  POLYGON ((-117.03235 48.99920, -117.13490 48.9...
1              NM  POLYGON ((-106.52805 31.78389, -106.52706 31.7...
2              MA  POLYGON ((-71.08857 41.43131, -71.08504 41.433...
3              UT  POLYGON ((-114.04148 41.99387, -114.04137 41.9...
4              AR  POLYGON ((-91.16609 33.00429, -91.16637 33.010...

In [28]:
#merging the geojson dataframe created in Plot 4, having statecode and geometry with health_spending_bystate_df 

healthspending_map = geojson.merge(health_spending_bystate_df,how="inner",left_on="ste_stusps_code",right_on="state_code")
healthspending_map = healthspending_map[~uninsured_map['geometry'].isna()]
healthspending_map = healthspending_map.dropna()
healthspending_map.head()

ste_stusps_code                                           geometry  \
0              WA  POLYGON ((-117.03235 48.99920, -117.13490 48.9...   
1              NM  POLYGON ((-106.52805 31.78389, -106.52706 31.7...   
2              MA  POLYGON ((-71.08857 41.43131, -71.08504 41.433...   
3              UT  POLYGON ((-114.04148 41.99387, -114.04137 41.9...   
4              AR  POLYGON ((-91.16609 33.00429, -91.16637 33.010...   

        Location   latitude   longitude  Health Spending per Capita state_code  
0     Washington  47.035805 -122.905014                      8964.0         WA  
1     New Mexico  35.682240 -105.939728                      8459.0         NM  
2  Massachusetts  42.358162  -71.063698                     12729.0         MA  
3           Utah  40.777477 -111.888237                      7193.0         UT  
4       Arkansas  34.746613  -92.288986                      8853.0         AR

In [29]:

#make an empty map
us_map = folium.Map(location=[40, -96], zoom_start=4,tiles='Stamen Toner')

#Create the choropleth map add it to the base map
#Average Heath Spending by State vs Highest and Least Deaths per 100k. 
#color scheme chosen yellow, green and blue

folium.Choropleth(
            geo_data="./Resources/georef-united-states-of-america-state.geojson",
            data=healthspending_map,
            columns=['state_code', 'Health Spending per Capita'],  #Here we tell folium to get the state codes and plot uninsured % for each state
            key_on='feature.properties.ste_stusps_code', #Here we grab the geometries/state boundaries from the geojson file using the key 'ste_stusps_code' which is the same as state code
            fill_color='YlGnBu',
            nan_fill_color="White", #Use white color if there is no data available for the state
            fill_opacity=0.7,
            line_opacity=0.2,
            legend_name='Avg Health Spending per Capita', 
            highlight=True,
            line_color='black').add_to(us_map) 

title_html = '''
             <h3 align="center" style="font-size:20px"><b>Average Health spending by State vs Least and Highest Deaths per 100k</b></h3>
             '''
us_map.get_root().html.add_child(folium.Element(title_html))


#red-icons/ markers for states with highest deaths per capita = Top 5
for index, location_info in mortality_bystate_df.head().iterrows():
    marker = folium.Marker([location_info["latitude"], location_info["longitude"]], 
                  popup="Deaths per 100k: " + str(location_info["Deaths per 100k"]), icon=folium.Icon(color="red", icon="plus-sign"), 
                tooltip = "State: {}<br> Click for more".format(location_info["Location"]))
    marker.add_to(us_map)

#blue-icons/ markers for states with least deaths per capita = Bottom 5    
for index, location in mortality_bystate_df.tail().iterrows():
    marker = folium.Marker([location["latitude"], location["longitude"]], 
                  popup="Deaths per 100k: " + str(location["Deaths per 100k"]), icon=folium.Icon(color="orange", icon="plus-sign"), 
                tooltip = "State: {}<br> Click for more".format(location["Location"]))
    marker.add_to(us_map)                           


us_map

#us_map.save('Plot 5-choropleth-map-with-folium.html')
 